In [43]:
import pandas as pd
import numpy as np
import pickle
import sklearn
import nltk
from nltk.corpus import wordnet
from tqdm import tqdm_notebook as tqdm

#load data
features = np.load('features.npy')
labels = np.load('labels.npy')
X_train = np.load('X_train.npy')
y_train = np.load('y_train.npy')
X_test = np.load('X_test.npy')
y_test = np.load('y_test.npy')
indices_train = np.load('indices_train.npy')
indices_test = np.load('indices_test.npy')

df = pd.read_pickle('dt_clean.pkl')
category_id_df = pd.read_pickle('category_id_df.pkl')
with open('id_to_category.pickle', 'rb') as handle:
    id_to_category = pickle.load(handle)
with open('category_to_id.pickle', 'rb') as handle:
    category_to_id = pickle.load(handle)

In [44]:
#linear models
from sklearn.linear_model import LogisticRegression, SGDClassifier, Perceptron

#LDA
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis, QuadraticDiscriminantAnalysis

#SVM
from sklearn.svm import SVC, LinearSVC

#KNN
from sklearn.neighbors import KNeighborsClassifier

#GP
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.gaussian_process.kernels import RBF

#NAIVE BAYES
from sklearn.naive_bayes import MultinomialNB, GaussianNB

#DT
from sklearn.tree import DecisionTreeClassifier

#ENSEMBLE
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier, VotingClassifier
    #BOOSTING
import xgboost

#NEURAL NETWORK
from sklearn.neural_network import MLPClassifier

from sklearn.model_selection import cross_val_score

In [45]:
from sklearn.naive_bayes import MultinomialNB, BernoulliNB
from sklearn.linear_model import RidgeClassifier
from sklearn.linear_model import PassiveAggressiveClassifier
from sklearn.neighbors import NearestCentroid

In [46]:
import numpy as np
import pandas as pd
import pickle
model = pickle.load(open('model.sav', 'rb'))

import matplotlib.pyplot as plt
from sklearn.metrics import (brier_score_loss, precision_score, recall_score, f1_score)
from sklearn.calibration import CalibratedClassifierCV, calibration_curve
from sklearn.model_selection import train_test_split

In [47]:
texts = ["i get an error when logging in G3 rms please advice",
         "On Dec 29 I set an overbooking limit of 5 rooms on CQN's. When I checked today (Dec 31) it is still not showing on PMS. Furthermore, we are in read-only mode and I cannot make any changes. I do not know how long this has been the case but I am concerned it has been for the last two days, which is why my changes have not taken effect. Please advise urgently. See screenshots for reference.",
         "logger"
        ]

In [48]:
import re
import string
def clean_text_round1(text):
    #Make text lowercase, remove leading spaces
    text = text.strip().lower()
    # remove HTML tags
    text = re.sub(r'<.*?>', '', text)
    #remove text in square brackets
    text = re.sub('\[.*?\]', '', text)
    # remove the characters [\], ['] and ["]
    text = re.sub(r"\\", "", text)    
    text = re.sub(r"\'", "", text)    
    text = re.sub(r"\"", "", text) 
    #remove punctuation
    text = re.sub('[%s]' % re.escape(string.punctuation), '', text)
    #remove words containing numbers
    text = re.sub('\w*\d\w*', '', text)
    #Get rid of some additional punctuation
    text = re.sub('[‘’“”…]', '', text)
    #remove next line '\n'
    text = re.sub('\n', '', text)
    #remove duplicate white spaces
    text = re.sub(' +', ' ', text)
    return text
round1 = lambda x: clean_text_round1(x)

In [49]:
text = map(round1, texts)
with open('id_to_category.pickle', 'rb') as handle:
    id_to_category = pickle.load(handle)
df = pd.read_pickle('dt_clean.pkl')
with open('data.pickle', 'rb') as f:
    stop_words = pickle.load(f)
    
from sklearn.feature_extraction.text import TfidfVectorizer
tfidf = TfidfVectorizer(analyzer='word', sublinear_tf=True, norm='l2', encoding='latin-1', ngram_range=(1,2), stop_words=stop_words)
tfidf_temp = tfidf.fit_transform(df.content).toarray()

In [51]:
text_features = tfidf.transform(text)
predictions = model.predict(text_features)
for text, predicted in zip(texts, predictions):
  print('"{}"'.format(text))
  print("  - Predicted as: '{}'".format(id_to_category[predicted]))
  print("")

ValueError: Found array with 0 sample(s) (shape=(0, 44740)) while a minimum of 1 is required.

In [ ]:
from sklearn.calibration import CalibratedClassifierCV
cal_pac = CalibratedClassifierCV(base_estimator=model, cv="prefit")
cal_pac.fit(X_train, y_train)
print(cal_pac.predict_proba(text_features))

In [ ]:
ds=pd.DataFrame(cal_pac.predict_proba(text_features)*100, columns = category_id_df['category'])
ds

In [ ]:
df[df.content.str.lower().str.contains('logger')].category.value_counts()